In [2]:
from lumibot.brokers import Alpaca
from lumibot.backtesting import YahooDataBacktesting
from lumibot.strategies.strategy import Strategy
from lumibot.traders import Trader
from datetime import datetime
from alpaca_trade_api import REST
from timedelta import Timedelta 
from finbert_utils import estimate_sentiment

c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
API_KEY= 'PKHZJKOINCDXO7SC97SR'
API_SECRET="ozNVizrfhTpDEhug0Hy7Ydm4Hhtd6w5LfbTOuMnn"
BASE_URL = 'https://paper-api.alpaca.markets/v2'

ALPACA_CREDS = {
    'API_KEY':API_KEY,
    'API_SECRET':API_SECRET,
    'PAPER':True
}
start_date=datetime(2023,1,1)#used for tastcase for stock between these days
end_date=datetime(2023,12,31)


        

In [14]:
class MLTrader(Strategy):
    def initialize(self,symbol:str="SPY",cash_at_risk: float=0.5):
        self.symbol = symbol
        self.sleeptime = '24H'#how frequently we are gonna trade
        self.last_trade = None#capture what the last trade is to undo our buys
        self.cash_at_risk = cash_at_risk
        self.api= REST(base_url=BASE_URL,key_id=API_KEY,secret_key=API_SECRET)
    def position_sizing(self):#everytime we get a new data, execute the trade
        cash =self.get_cash()
        last_price = self.get_last_price(self.symbol)
        quantity = round(cash*self.cash_at_risk/last_price,0)
        return cash,last_price,quantity
    def get_dates(self):
        today = self.get_datetime()
        three_days_prior = today - Timedelta(days=3)
        return today.strftime('%Y-%m-%d'),three_days_prior.strftime('%Y-%m-%d')
    def get_sentiment(self):
        today,three_days_prior=self.get_dates()
        news = self.api.get_news(symbol=self.symbol,
                                 start=three_days_prior,
                                 end=today
                                )
        news = [ev.__dict__['_raw']['headline']for ev in news]
        probability,sentiment = estimate_sentiment(news)  
        return probability,sentiment   
    def on_trading_iteration(self):
        cash,last_price,quantity = self.position_sizing()
        probability,sentiment = self.get_sentiment()
        if cash>last_price:
            if sentiment == 'positive' and probability>.999:
                if self.last_trade == 'sell':
                    self.sell_all()
            order = self.create_order(
                self.symbol,
                quantity,
                'buy',
                type='bracket',
                take_profit_price=last_price*1.20,
                stop_loss_price=last_price*.95
            )
            self.submit_order(order)
            self.last_trade = 'buy'
        elif sentiment == 'negative' and probability >.999:
                if self.last_trade == 'buy':
                    self.sell_all()
                order = self.create_order(
                    self.symbol,
                    quantity,
                    'sell',
                    type='bracket',
                    take_profit_price=last_price*.8,
                    stop_loss_price=last_price*1.05
                )
                self.submit_order(order)
                self.last_trade = 'sell'


In [1]:
broker = Alpaca(ALPACA_CREDS)
strategy = MLTrader(name='mlstrat',broker=broker,parameters={'symbol':"SPY",'cash_at_risk':.5})
strategy.backtest(
    YahooDataBacktesting,
    start_date,
    end_date,
    parameters={'symbol':"SPY"}
)

NameError: name 'Alpaca' is not defined

Starting backtest for MLTrader...


Exception in thread MLTrader:
Traceback (most recent call last):
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\lumibot\strategies\strategy_executor.py", line 818, in run
    self._initialize()
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\lumibot\strategies\strategy_executor.py", line 274, in func_output
    result = func_input(self, *args, **kwargs)
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\lumibot\strategies\strategy_executor.py", line 329, in _initialize
    self.strategy.initialize(**safe_params_to_pass)
  File "C:\Users\kushw\AppData\Local\Temp\ipykernel_33484\3692094755.py", line 7, in initialize
NameError: name 'REST' is not defined



Creating indicators plot...


{}

In [ ]:
API_KEY= 'PKJHYUEHVBESQUYLQJ5Z'
API_SECRET="tukk96fcOY5cIyBdKCTTsyoA8dpR0M5DzS8WFjXF"
BASE_URL = 'https://paper-api.alpaca.markets/v2'

ALPACA_CREDS = {
    'API_KEY':API_KEY,
    'API_SECRET':API_SECRET,
    'PAPER':True
}
start_date=datetime(2023,11,15)
end_date=datetime(2023,12,31)
class MLTrader(Strategy):
    def initialize(self,symbol:str="SPY"):
        self.symbol = symbol
        self.sleeptime = '24H'
        self.last_trade = None
        
    def on_trading_iteration(self):
        if self.last_trade==None:
            order = self.create_order(
                self.symbol,
                10,
                'buy',
                type='market')
            self.submit_order(order)
            self.last_trade='buy'
broker = Alpaca(ALPACA_CREDS)
strategy = MLTrader(name='mlstrat',broker=broker,parameters={'symbol':"SPY"})
strategy.backtest(
    YahooDataBacktesting,
    start_date,
    end_date,
    parameters={'symbol':"SPY"}
)


Starting backtest for MLTrader...


INFO:backtest_stats:Starting backtest...


Progress ||  51.45%  [Elapsed: 0:00:02 ETA: 0:00:02] Portfolio Val: 100,073.50

c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\lumibot\backtesting\backtesting_broker.py:514: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  open = ohlc.df.open[-1]
c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\lumibot\backtesting\backtesting_broker.py:515: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  high = ohlc.df.high[-1]
c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\lumibot\backtesting\backtesting_broker.py:516: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). 

Progress || 100.00%  [Elapsed: 0:00:02 ETA: 0:00:00] Portfolio Val: 100,282.86
Creating trades plot...

Creating indicators plot...

Creating tearsheet...


c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning:

The behavior of DataFrame.prod with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)

c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning:

The behavior of DataFrame.prod with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)

c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning:

The behavior of DataFrame.prod with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)



{'cagr': 0.02319122760035852,
 'volatility': 0.003461950125154027,
 'sharpe': -8.451528819737266,
 'max_drawdown': {'drawdown': 0.0003003285405203337,
  'date': Timestamp('2023-12-15 09:30:00-0500', tz='America/New_York')},
 'romad': 77.21952619014695,
 'total_return': 0.0028286004882818183}

2024-04-21 07:22:57,932: alpaca.trading.stream: ERROR: error during websocket communication: [Errno 11001] getaddrinfo failed
Traceback (most recent call last):
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\alpaca\trading\stream.py", line 168, in _run_forever
    await self._start_ws()
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\alpaca\trading\stream.py", line 128, in _start_ws
    await self._connect()
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\alpaca\trading\stream.py", line 59, in _connect
    self._ws = await websockets.connect(self._endpoint, **self._websocket_params)
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\websockets\legacy\client.py", line 647, in __await_impl_timeout__
    return await self.__await_impl__()
  File "c:\Users\kushw\miniconda3\envs\tgpu\lib\site-packages\websockets\legacy\client.py", line 651, in __await_impl__
    _transport, _protocol = await self._create_connection()
  File "c:\Users\kus